# Import Statements

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from folium import plugins
from folium.plugins import HeatMap
from datetime import datetime
from datetime import timedelta
import math
import random
import timeit

---

# Bicycle Positional Data

## First look
Firstly we read our data in order to determine the attributes given and their meaning.

In [2]:
#First we read our data
marburg = pd.read_csv("../0_data/marburg.csv")
duisburg = pd.read_csv("../0_data/duisburg.csv")

In [3]:
marburg.head() #first tuples of the dataset

day      time  b_number     city              trip_duration  \
0  2019-07-04  13:29:00     11070  marburg  0 days 00:41:00.000000000   
1  2019-07-06  16:53:00     11070  marburg  0 days 00:19:00.000000000   
2  2019-07-06  17:18:00     11070  marburg  0 days 01:01:00.000000000   
3  2019-07-06  20:11:00     11070  marburg  0 days 00:30:00.000000000   
4  2019-07-07  08:47:00     11070  marburg  0 days 00:12:00.000000000   

    orig_lat  orig_lng   dest_lat  dest_lng  
0  50.808070  8.775351  50.810971  8.774241  
1  50.798656  8.752965  50.805809  8.782821  
2  50.805809  8.782821  50.822927  8.774681  
3  50.819957  8.773736  50.785589  8.779437  
4  50.785589  8.779437  50.795224  8.763266

In [4]:
duisburg.head() #first tuples of the dataset

day      time  b_number      city              trip_duration  \
0  2019-05-27  14:48:00       683  duisburg  0 days 01:13:00.000000000   
1  2019-05-27  17:20:00       683  duisburg  0 days 00:44:00.000000000   
2  2019-05-28  08:19:00       683  duisburg  0 days 00:06:00.000000000   
3  2019-06-04  09:13:00       683  duisburg  0 days 00:12:00.000000000   
4  2019-06-05  09:08:00       683  duisburg  0 days 00:52:00.000000000   

    orig_lat  orig_lng   dest_lat  dest_lng  
0  51.425986  6.764934  51.428250  6.785619  
1  51.428250  6.785619  51.431444  6.759110  
2  51.431444  6.759110  51.433334  6.768420  
3  51.434073  6.762675  51.431444  6.759110  
4  51.431444  6.759110  51.439263  6.782880

As we can see there are 9 attributes in our dataset. These are the coordinates where the bicycle was borrowed  _(orig_lat, orig_lng)_ and where it was returned _(dest_lat, dest_lng)_. Lat stands for latitude and lng for longitude. Also we can see which bicycle was borrowed by the bicycle number _(b_number)_ and how long the trip was _(trip_duration)_. _Day time_ and _city_ are self explaining.

In [5]:
marburg.describe()

b_number      orig_lat       orig_lng      dest_lat       dest_lng
count  164205.000000  1.642050e+05  164205.000000  1.642050e+05  164205.000000
mean    11201.571858  2.465654e+02       8.771428  1.481188e+02       8.771390
std      1036.308122  3.966403e+04       0.009935  2.788458e+04       0.010200
min     11070.000000 -5.041531e+02       7.965424 -5.041531e+02       6.775276
25%     11132.000000  5.080472e+01       8.769918  5.080472e+01       8.769918
50%     11186.000000  5.080887e+01       8.773266  5.080887e+01       8.773262
75%     11240.000000  5.081395e+01       8.775086  5.081395e+01       8.775086
max     91202.000000  8.084779e+06      10.412875  8.063592e+06      10.199357

In [6]:
duisburg.describe()

b_number       orig_lat       orig_lng       dest_lat  \
count  132294.000000  132294.000000  132294.000000  132294.000000   
mean    74057.925174      51.430102       6.781636      51.430152   
std     98716.954856       0.018423       0.055535       0.019182   
min       683.000000      50.778667       6.403277      50.778667   
25%     51197.000000      51.427297       6.769777      51.427297   
50%     51510.000000      51.429424       6.778436      51.429424   
75%     51589.000000      51.433066       6.791842      51.433066   
max    501599.000000      51.585475       8.775398      52.934196   

            dest_lng  
count  132294.000000  
mean        6.781890  
std         0.056420  
min         4.990632  
25%         6.769546  
50%         6.778436  
75%         6.791842  
max         8.775398

In the generated descriptive statistics above can be seen that some min and max values (e.g. -504 as min for orig_lat in Marburg) clearly indicate erroneous data. Therefore it must be cleaned in order to achieve more precise calculations in the future.

In [7]:
len(marburg)-len(marburg.dropna()) #comparing length original dataset to length of set, where null values are dropped

0

In [8]:
len(duisburg)-len(duisburg.dropna())  #comparing length of original dataset to length of set, where null values are dropped

0

By comparing the difference in the length of the original dataset and the dropna-dataset, it can be ensured that there are no null values.

## Cleaning coordinates Duisburg

In [9]:
# Zipping latitudes and longitudes together in an new column
duisburg["orig"] = list(zip(duisburg["orig_lat"].round(4),duisburg["orig_lng"].round(4)))
duisburg["dest"] = list(zip(duisburg["dest_lat"].round(4),duisburg["dest_lng"].round(4)))

duisburg.head()

day      time  b_number      city              trip_duration  \
0  2019-05-27  14:48:00       683  duisburg  0 days 01:13:00.000000000   
1  2019-05-27  17:20:00       683  duisburg  0 days 00:44:00.000000000   
2  2019-05-28  08:19:00       683  duisburg  0 days 00:06:00.000000000   
3  2019-06-04  09:13:00       683  duisburg  0 days 00:12:00.000000000   
4  2019-06-05  09:08:00       683  duisburg  0 days 00:52:00.000000000   

    orig_lat  orig_lng   dest_lat  dest_lng               orig  \
0  51.425986  6.764934  51.428250  6.785619   (51.426, 6.7649)   
1  51.428250  6.785619  51.431444  6.759110  (51.4283, 6.7856)   
2  51.431444  6.759110  51.433334  6.768420  (51.4314, 6.7591)   
3  51.434073  6.762675  51.431444  6.759110  (51.4341, 6.7627)   
4  51.431444  6.759110  51.439263  6.782880  (51.4314, 6.7591)   

                dest  
0  (51.4283, 6.7856)  
1  (51.4314, 6.7591)  
2  (51.4333, 6.7684)  
3  (51.4314, 6.7591)  
4  (51.4393, 6.7829)

In [10]:
Du_map = folium.Map(location=(51.430102, 6.781636),  #the orig mean values as location coordinates
                       zoom_start=7, control_scale=True, max_zoom=20)
Du_map.add_child(plugins.HeatMap(duisburg["orig"], radius=15)) #adding heatmap points with the orig coordinates
Du_map.add_child(plugins.HeatMap(duisburg["dest"], radius=15)) #adding heatmap points with the dest coordinates

Du_map #showing Map

As visaulized on the heatmap above some coordinates are far away from Duisburg. Hence we limit our data to entries that are located in the city and some sensible distance away.

We take a look a the official boundaries NextBike defined for the metropolradruhr cities. In these cities users are free to travel. So we restrict the area of our trips to metropolradruhrs service area.

In [11]:
import urllib
import json

In [12]:
with urllib.request.urlopen("https://api.nextbike.net/maps/nextbike-live.json?list_cities=1") as url:
    next_bike_countries = json.loads(url.read().decode())

for country in next_bike_cities['countries']:
    if country['name'] == 'metropolradruhr Germany':
        metropolrad = country
        
south_west_coords = [city['bounds']['south_west'] for city in metropolrad['cities']]
north_east_coords = [city['bounds']['north_east'] for city in metropolrad['cities']]

NameError: name 'next_bike_cities' is not defined

In [ ]:
south_west_lat = [coord['lat'] for coord in south_west_coords]
south_west_lng = [coord['lng'] for coord in south_west_coords]

north_east_lat = [coord['lat'] for coord in north_east_coords]
north_east_lng = [coord['lng'] for coord in north_east_coords]

In [ ]:
south_west_min_lat = min(south_west_lat)
south_west_min_lng = min(south_west_lng)

north_east_max_lat = max(north_east_lat)
north_east_max_lng = max(north_east_lng)

In [ ]:
duisburg = duisburg[ (duisburg["orig_lat"]>south_west_min_lat) & (duisburg["orig_lat"] < north_east_max_lat) #setting limits for orig_lat
                & (duisburg["orig_lng"]>south_west_min_lng) & (duisburg["orig_lng"] < north_east_max_lng) #setting limits for orig_lng
                & (duisburg["dest_lat"]>south_west_min_lat) & (duisburg["dest_lat"] < north_east_max_lat) #setting limits for dest_lat
                & (duisburg["dest_lng"]>south_west_min_lng) & (duisburg["dest_lng"] < north_east_max_lng) ] #setting limits for dest_lng

In [ ]:
Du_map = folium.Map(location=(51.44, 6.83), #the middle of limits as coordinates
                       zoom_start=10, control_scale=True, max_zoom=20)
Du_map.add_child(plugins.HeatMap(duisburg["orig"], radius=15)) #adding heatmap points with the cleaned orig coordinates
Du_map.add_child(plugins.HeatMap(duisburg["dest"], radius=15)) #adding heatmap points with the cleaned dest coordinates

Du_map #showing Map

Now we can drop the columns with the latitudes and longitudes because we only need them zipped as map points.

In [ ]:
duisburg.drop(columns=['orig_lat','orig_lng','dest_lat','dest_lng'], axis=1, inplace = True)
duisburg.head()

## Cleaning Coordinates Marburg

In [ ]:
#Zipping latitudes and longitudes together in an new column
marburg["orig"] = list(zip(marburg["orig_lat"].round(4),marburg["orig_lng"].round(4))) 
marburg["dest"] = list(zip(marburg["dest_lat"].round(4),marburg["dest_lng"].round(4)))

marburg.head()

In [ ]:
Ma_map = folium.Map(location=(50.8021728, 8.7667933), #the coordinates from 'https://www.laengengrad-breitengrad.de/gps-koordinaten-von-marburg' 
                       zoom_start=1, control_scale=True, max_zoom=20)
Ma_map.add_child(plugins.HeatMap(marburg["orig"], radius=15)) #adding heatmap points with the orig coordinates
Ma_map.add_child(plugins.HeatMap(marburg["orig"], radius=15)) #adding heatmap points with the orig coordinates
    
Ma_map

Analog to Duisburg there is erroneous positional data. As seen on the heatmap there are some entries very far away from Marburg and even land. Therefore analog to Duisburg we limit our data to coordinates that are in and around Marburg.

In [ ]:
marburg = marburg[ (marburg["orig_lat"]>50.72) & (marburg["orig_lat"] < 50.89) #setting limits for orig_lat
                & (marburg["orig_lng"]>8.62) & (marburg["orig_lng"] < 8.86) #setting limits for orig_lng
                & (marburg["dest_lat"]>50.72) & (marburg["dest_lat"] < 50.89) #setting limits for dest_lat
                & (marburg["dest_lng"]>8.62) & (marburg["dest_lng"] < 8.86) ] #setting limits for dest_lng

In [ ]:
Ma_map = folium.Map(location=(50.81, 8.74), #the middle of limits as coordinates
                       zoom_start=10, control_scale=True, max_zoom=20)
Ma_map.add_child(plugins.HeatMap(marburg["orig"], radius=15)) #adding heatmap points with the cleaned orig coordinates
Ma_map.add_child(plugins.HeatMap(marburg["dest"], radius=15)) #adding heatmap points with the cleaned dest coordinates
 
Ma_map

In [ ]:
marburg.drop(columns=['orig_lat','orig_lng','dest_lat','dest_lng'], axis=1, inplace = True)
marburg.head()

## Setting Index, extracting Weekday and Hour

In the next steps we will merge the given strings _(day)_ and _(time)_ and create a datetime object from the merged string as well as set it as index and extract weekday and hour values for convenience of further calculations.

In [ ]:
duisburg['datetime'] = duisburg['day'] + duisburg['time']
duisburg['datetime'] = pd.to_datetime(duisburg['datetime'], format='%Y-%m-%d%H:%M:%S')
duisburg["weekday"] = duisburg['datetime'].dt.weekday
duisburg["hour"] = duisburg['datetime'].dt.hour
duisburg.set_index(duisburg['datetime'], inplace=True)
duisburg.drop(columns=['datetime'], axis=1, inplace = True)
duisburg.head()

The corresponding changes will now be made to the Marburg dataset.

In [ ]:
marburg['datetime'] = marburg['day'] + marburg['time']
marburg['datetime'] = pd.to_datetime(marburg['datetime'], format='%Y-%m-%d%H:%M:%S')
marburg["weekday"] = marburg['datetime'].dt.weekday
marburg["hour"] = marburg['datetime'].dt.hour
marburg.set_index(marburg['datetime'], inplace=True)
marburg.drop(columns=['datetime'], axis=1, inplace = True)
marburg.head()

## Cleaning up the "trip_duration"

In [ ]:
#Lets take a look at how the trip_duration column looks for Duisburg
duisburg["trip_duration"]

In [ ]:
duisburg["trip_duration"].max()

As seen above the longest trip taken lasted 3 hours. Hence, we can reduce the trip duration to only show hours instead of days.

In [ ]:
#We can clean up a lot of the unneccessary data

duisburg["trip_duration"] = duisburg["trip_duration"].str.replace('0 days 0', '')
duisburg["trip_duration"] = duisburg["trip_duration"].str.replace(':00.000000000', '')

duisburg["trip_duration"]

In [ ]:
#The trip_duration column for Marburg looks pretty cluttered as well
marburg["trip_duration"]

In [ ]:
#We can clean up a lot of the unneccessary data here as well

marburg["trip_duration"] = marburg["trip_duration"].str.replace('0 days 0', '')
marburg["trip_duration"] = marburg["trip_duration"].str.replace(':00.000000000', '')

marburg["trip_duration"]

## Convert object "trip_duration" to single value "trip_duration_mins"

In [ ]:
#Changing the trip_duration from an object to a panda datetime format, which will make it easier to convert it to a single value for minutes in the following cells.
duisburg["trip_duration"] = pd.to_datetime(duisburg["trip_duration"])
duisburg["trip_duration"]

In [ ]:
#Isolating the value for hours and minutes in seperate columns.
duisburg["trip_duration_mins"] = duisburg["trip_duration"].apply(lambda x: x.minute)
duisburg["trip_duration_hour"] = duisburg["trip_duration"].apply(lambda x: x.hour)
duisburg.head(5)

In [ ]:
#For every hour in trip_duration_hour we are adding 60 mins to the value of trip_duration_mins.
duisburg["trip_duration_mins"] = duisburg["trip_duration_mins"] + (duisburg["trip_duration_hour"] * 60)
duisburg.describe()

In [ ]:
#Now we can drop the columns trip_duration and trip_duration_hour, as we have the total ride time in minutes in the column trip_duration_mins now.
duisburg.drop(columns=['trip_duration','trip_duration_hour'], axis=1, inplace = True)
duisburg.head()

In [ ]:
#In this cell we will do all of that for the Marburg data as well
marburg["trip_duration"] = pd.to_datetime(marburg["trip_duration"])
marburg["trip_duration_mins"] = marburg["trip_duration"].apply(lambda x: x.minute)
marburg["trip_duration_hour"] = marburg["trip_duration"].apply(lambda x: x.hour)
marburg["trip_duration_mins"] = marburg["trip_duration_mins"] + (marburg["trip_duration_hour"] * 60)
marburg.drop(columns=['trip_duration','trip_duration_hour'], axis=1, inplace = True)
marburg.head()

In [ ]:
#we save our cleaned data in the pickle format, so that the datatypes will remain the same
marburg.to_pickle('../0_data/marburg_clean.pkl')
duisburg.to_pickle('../0_data/duisburg_clean.pkl')